In [1]:
import polars as pl
import geopandas as gpd
import pyarrow

In [2]:
t_finess = pl.read_csv("../data/t-finess.csv", ignore_errors=True)

In [3]:
t_finess.head()

shape: (5, 85)
┌────────────┬────────────┬──────────┬─────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ source     ┆ date_maj   ┆ finess   ┆ finess8 ┆ … ┆ geoloc_38 ┆ geoloc_38 ┆ geoloc_43 ┆ geoloc_43 │
│ ---        ┆ ---        ┆ ---      ┆ ---     ┆   ┆ 57_x      ┆ 57_y      ┆ 26_long   ┆ 26_lat    │
│ str        ┆ str        ┆ i64      ┆ i64     ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│            ┆            ┆          ┆         ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞════════════╪════════════╪══════════╪═════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ DataSanté  ┆ 2025-06-02 ┆ 10000016 ┆ 1000001 ┆ … ┆ 683488.87 ┆ 5.8386e6  ┆ 6.139885  ┆ 46.362063 │
│ (doc en    ┆            ┆          ┆         ┆   ┆ 2         ┆           ┆           ┆           │
│ ligne sur  ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ da…        ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ DataSanté  ┆ 2025-06-02 ┆ 10000024 ┆ 1000002 ┆ … ┆ 579794.98 ┆ 5.8161e6  ┆ 5.208387  ┆ 46.222647 │
│ (doc en    ┆            ┆          ┆         ┆   ┆ 9         ┆           ┆           ┆           │
│ ligne sur  ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ da…        ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ DataSanté  ┆ 2025-06-02 ┆ 10000032 ┆ 1000003 ┆ … ┆ 632282.68 ┆ 5.7401e6  ┆ 5.679892  ┆ 45.748331 │
│ (doc en    ┆            ┆          ┆         ┆   ┆ 5         ┆           ┆           ┆           │
│ ligne sur  ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ da…        ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ DataSanté  ┆ 2025-06-02 ┆ 10000040 ┆ 1000004 ┆ … ┆ 624339.26 ┆ 5.8042e6  ┆ 5.608535  ┆ 46.148832 │
│ (doc en    ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ ligne sur  ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ da…        ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ DataSanté  ┆ 2025-06-02 ┆ 10000057 ┆ 1000005 ┆ … ┆ 626433.51 ┆ 5.8245e6  ┆ 5.627348  ┆ 46.275059 │
│ (doc en    ┆            ┆          ┆         ┆   ┆ 4         ┆           ┆           ┆           │
│ ligne sur  ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
│ da…        ┆            ┆          ┆         ┆   ┆           ┆           ┆           ┆           │
└────────────┴────────────┴──────────┴─────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [4]:
t_finess_clean = (t_finess
                  .filter(pl.col("etat") == "ACTUEL")
                  .filter(pl.col("statut_jur_etat") == "O")
                  .filter(pl.col("geoloc_legal_projection") == "L93_METROPOLE")
                  .with_columns(mco = (pl.col("san_med") == "OUI") | (pl.col("san_chir") == "OUI") | (pl.col("san_obs") == "OUI"))
                  .with_columns(ssr = (pl.col("san_smr") == "OUI"))
                  .with_columns(psy = (pl.col("san_psy") == "OUI"))
                  .with_columns(
                        forme_juridique = pl.when(
                                                pl.col("statut_jur_niv1_lib").str.to_lowercase().str.contains("public")
                                            ).then(pl.lit("public"))
                                            .when(
                                                pl.col("statut_jur_niv1_lib").str.to_lowercase().str.contains("privé")
                                            ).then(pl.lit("privé"))
                                            .otherwise(None)
                  )
                  .with_columns(dept = pl.col("finess").cast(pl.Utf8).str.slice(0, 2))
                        
)

In [5]:
t_finess_clean["etat"].value_counts()
t_finess_clean["forme_juridique"].value_counts()
t_finess_clean["dept"].value_counts()

t_finess_clean.shape

(150927, 90)

In [6]:
t_finess_clean = (t_finess_clean
                  .filter(pl.col("mco") | pl.col("ssr") | pl.col("psy"))
)

In [7]:
t_finess_clean.shape

(3731, 90)

In [8]:
cols_to_keep = [
        "finess",
        "rs",
        "mco",
        "ssr",
        "psy",
        "forme_juridique",
        "geoloc_4326_lat",
        "geoloc_4326_long"
]

In [9]:
t_finess_clean.select(pl.col(cols_to_keep))

shape: (3_731, 8)
┌───────────┬───────────────┬───────┬───────┬───────┬───────────────┬───────────────┬──────────────┐
│ finess    ┆ rs            ┆ mco   ┆ ssr   ┆ psy   ┆ forme_juridiq ┆ geoloc_4326_l ┆ geoloc_4326_ │
│ ---       ┆ ---           ┆ ---   ┆ ---   ┆ ---   ┆ ue            ┆ at            ┆ long         │
│ i64       ┆ str           ┆ bool  ┆ bool  ┆ bool  ┆ ---           ┆ ---           ┆ ---          │
│           ┆               ┆       ┆       ┆       ┆ str           ┆ f64           ┆ f64          │
╞═══════════╪═══════════════╪═══════╪═══════╪═══════╪═══════════════╪═══════════════╪══════════════╡
│ 10000024  ┆ CH DE         ┆ true  ┆ true  ┆ false ┆ public        ┆ 46.222647     ┆ 5.208387     │
│           ┆ FLEYRIAT      ┆       ┆       ┆       ┆               ┆               ┆              │
│ 10000032  ┆ CH BUGEY SUD  ┆ true  ┆ false ┆ false ┆ public        ┆ 45.748331     ┆ 5.679892     │
│ 10000065  ┆ CH DE TREVOUX ┆ true  ┆ true  ┆ false ┆ public        ┆ 45.941074     ┆ 4.771957     │
│           ┆ - MONTPENSIER ┆       ┆       ┆       ┆               ┆               ┆              │
│ 10000081  ┆ CH DU PAYS DE ┆ false ┆ true  ┆ false ┆ public        ┆ 46.322338     ┆ 6.057731     │
│           ┆ GEX           ┆       ┆       ┆       ┆               ┆               ┆              │
│ 10000099  ┆ CH DE         ┆ true  ┆ true  ┆ false ┆ public        ┆ 45.90663      ┆ 5.194669     │
│           ┆ MEXIMIEUX     ┆       ┆       ┆       ┆               ┆               ┆              │
│ …         ┆ …             ┆ …     ┆ …     ┆ …     ┆ …             ┆ …             ┆ …            │
│ 950786970 ┆ CENTRE DE     ┆ false ┆ false ┆ true  ┆ public        ┆ 48.942835     ┆ 2.243323     │
│           ┆ JOUR M BORAYU ┆       ┆       ┆       ┆               ┆               ┆              │
│ 950787119 ┆ HDJ CENTRE    ┆ false ┆ false ┆ true  ┆ privé         ┆ 48.989652     ┆ 2.262829     │
│           ┆ PSY LES       ┆       ┆       ┆       ┆               ┆               ┆              │
│           ┆ VIGNOLLES     ┆       ┆       ┆       ┆               ┆               ┆              │
│ 950787135 ┆ CENTRE PSYCHO ┆ false ┆ true  ┆ true  ┆ public        ┆ 49.144684     ┆ 2.310856     │
│           ┆ THERAPIQUE    ┆       ┆       ┆       ┆               ┆               ┆              │
│           ┆ LES OL…       ┆       ┆       ┆       ┆               ┆               ┆              │
│ 950807982 ┆ CLINIQUE      ┆ true  ┆ false ┆ false ┆ privé         ┆ 48.981269     ┆ 2.264429     │
│           ┆ CLAUDE        ┆       ┆       ┆       ┆               ┆               ┆              │
│           ┆ BERNARD       ┆       ┆       ┆       ┆               ┆               ┆              │
│ 950809293 ┆ HDJ HOPITAL   ┆ false ┆ false ┆ true  ┆ public        ┆ 49.145514     ┆ 2.290792     │
│           ┆ NOVO          ┆       ┆       ┆       ┆               ┆               ┆              │
│           ┆ SITEBEAUMONT  ┆       ┆       ┆       ┆               ┆               ┆              │
│           ┆ …             ┆       ┆       ┆       ┆               ┆               ┆              │
└───────────┴───────────────┴───────┴───────┴───────┴───────────────┴───────────────┴──────────────┘

In [10]:

# Convert to GeoDataFrame
t_finess_geo = gpd.GeoDataFrame(
    t_finess_clean.select(pl.col(cols_to_keep)).to_pandas(),
    geometry=gpd.points_from_xy(
        t_finess_clean.select(pl.col("geoloc_4326_long")).to_pandas()["geoloc_4326_long"],
        t_finess_clean.select(pl.col("geoloc_4326_lat")).to_pandas()["geoloc_4326_lat"]
    ),
    crs="EPSG:4326"
)

In [11]:
t_finess_geo

finess                                      rs    mco    ssr  \
0      10000024.0                          CH DE FLEYRIAT   True   True   
1      10000032.0                            CH BUGEY SUD   True  False   
2      10000065.0             CH DE TREVOUX - MONTPENSIER   True   True   
3      10000081.0                       CH DU PAYS DE GEX  False   True   
4      10000099.0                         CH DE MEXIMIEUX   True   True   
...           ...                                     ...    ...    ...   
3726  950786970.0                 CENTRE DE JOUR M BORAYU  False  False   
3727  950787119.0            HDJ CENTRE PSY LES VIGNOLLES  False  False   
3728  950787135.0    CENTRE PSYCHOTHERAPIQUE LES OLIVIERS  False   True   
3729  950807982.0                 CLINIQUE CLAUDE BERNARD   True  False   
3730  950809293.0  HDJ HOPITAL NOVO SITEBEAUMONT SUR OISE  False  False   

        psy forme_juridique  geoloc_4326_lat  geoloc_4326_long  \
0     False          public        46.222647          5.208387   
1     False          public        45.748331          5.679892   
2     False          public        45.941074          4.771957   
3     False          public        46.322338          6.057731   
4     False          public        45.906630          5.194669   
...     ...             ...              ...               ...   
3726   True          public        48.942835          2.243323   
3727   True           privé        48.989652          2.262829   
3728   True          public        49.144684          2.310856   
3729  False           privé        48.981269          2.264429   
3730   True          public        49.145514          2.290792   

                      geometry  
0     POINT (5.20839 46.22265)  
1     POINT (5.67989 45.74833)  
2     POINT (4.77196 45.94107)  
3     POINT (6.05773 46.32234)  
4     POINT (5.19467 45.90663)  
...                        ...  
3726  POINT (2.24332 48.94284)  
3727  POINT (2.26283 48.98965)  
3728  POINT (2.31086 49.14468)  
3729  POINT (2.26443 48.98127)  
3730  POINT (2.29079 49.14551)  

[3731 rows x 9 columns]

In [12]:
import folium
from folium import plugins

# Create a base map centered on France
m = folium.Map(
    location=[46.603354, 1.888334],  # Center of France
    zoom_start=6,
    tiles='OpenStreetMap'
)

# Define colors for different types of facilities
def get_color(row):
    if row['mco'] and row['ssr'] and row['psy']:
        return 'purple'  # All three types
    elif row['mco'] and row['ssr']:
        return 'red'     # MCO + SSR
    elif row['mco'] and row['psy']:
        return 'orange'  # MCO + PSY
    elif row['ssr'] and row['psy']:
        return 'yellow'  # SSR + PSY
    elif row['mco']:
        return 'blue'    # MCO only
    elif row['ssr']:
        return 'green'   # SSR only
    elif row['psy']:
        return 'pink'    # PSY only
    else:
        return 'gray'    # None (shouldn't happen with our filter)

# Add points to the map
for idx, row in t_finess_geo.iterrows():
    popup_text = f"""
    <b>{row['rs']}</b><br>
    FINESS: {row['finess']}<br>
    Forme juridique: {row['forme_juridique']}<br>
    MCO: {'✓' if row['mco'] else '✗'}<br>
    SSR: {'✓' if row['ssr'] else '✗'}<br>
    PSY: {'✓' if row['psy'] else '✗'}
    """
    
    folium.CircleMarker(
        location=[row['geoloc_4326_lat'], row['geoloc_4326_long']],
        radius=5,
        popup=folium.Popup(popup_text, max_width=300),
        color='black',
        weight=1,
        fillColor=get_color(row),
        fillOpacity=0.7
    ).add_to(m)

# Add a legend
legend_html = '''
<div style="position: fixed; 
            bottom: 50px; left: 50px; width: 200px; height: 180px; 
            background-color: white; border:2px solid grey; z-index:9999; 
            font-size:14px; padding: 10px">
<p><b>Facility Types</b></p>
<p><i class="fa fa-circle" style="color:blue"></i> MCO only</p>
<p><i class="fa fa-circle" style="color:green"></i> SSR only</p>
<p><i class="fa fa-circle" style="color:pink"></i> PSY only</p>
<p><i class="fa fa-circle" style="color:red"></i> MCO + SSR</p>
<p><i class="fa fa-circle" style="color:orange"></i> MCO + PSY</p>
<p><i class="fa fa-circle" style="color:yellow"></i> SSR + PSY</p>
<p><i class="fa fa-circle" style="color:purple"></i> All three</p>
</div>
'''
m.get_root().html.add_child(folium.Element(legend_html))

# Display the map
m
